In [1]:
!python -m pip install mysql-connector-python


Looking in indexes: https://pypi.org/simple, https://pypi.ngc.nvidia.com



[notice] A new release of pip is available: 24.2 -> 25.1.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [8]:
import mysql.connector
import pickle  

# Connect to MySQL
conn_config = {
    'host': '127.0.0.1',
    'user': 'centralAuth',
    'password': 'messi10',
    'database': 'fl_database'
}
conn = mysql.connector.connect(**conn_config)
cursor = conn.cursor()


cursor.execute("""
    SELECT client_id, model_blob, accuracy, loss, macro_f1, recall_minority, f1_minority, f1_majority, fit_status
    FROM client_updates
    WHERE model_id =2 and round_num = 2 
""")
client_updates = cursor.fetchall()
client_updates


[('2',
  b'\x80\x04\x95\x8d\x03\x00\x00\x00\x00\x00\x00\x8c\x0fxgboost.sklearn\x94\x8c\rXGBClassifier\x94\x93\x94)\x81\x94}\x94(\x8c\x0cn_estimators\x94M,\x01\x8c\tobjective\x94\x8c\x0fbinary:logistic\x94\x8c\tmax_depth\x94K\x07\x8c\nmax_leaves\x94N\x8c\x07max_bin\x94N\x8c\x0bgrow_policy\x94N\x8c\rlearning_rate\x94G?\xc9\x99\x99\x99\x99\x99\x9a\x8c\tverbosity\x94N\x8c\x07booster\x94N\x8c\x0btree_method\x94N\x8c\x05gamma\x94G@\x00(\xf5\xc2\x8f\\)\x8c\x10min_child_weight\x94N\x8c\x0emax_delta_step\x94N\x8c\tsubsample\x94G?\xed\x1e\xb8Q\xeb\x85\x1f\x8c\x0fsampling_method\x94N\x8c\x10colsample_bytree\x94G?\xec(\xf5\xc2\x8f\\)\x8c\x11colsample_bylevel\x94N\x8c\x10colsample_bynode\x94N\x8c\treg_alpha\x94N\x8c\nreg_lambda\x94N\x8c\x10scale_pos_weight\x94K\x04\x8c\nbase_score\x94N\x8c\x07missing\x94G\x7f\xf8\x00\x00\x00\x00\x00\x00\x8c\x11num_parallel_tree\x94N\x8c\x0crandom_state\x94K*\x8c\x06n_jobs\x94N\x8c\x14monotone_constraints\x94N\x8c\x17interaction_constraints\x94N\x8c\x0fimportance_ty

In [9]:
import pickle

models = []
metrics = []

for row in client_updates:
    client_id, model_blob, accuracy, loss, macro_f1, recall_minority, f1_minority, f1_majority, fit_status = row
    model = pickle.loads(model_blob)
    models.append((client_id, model))
    metrics.append({
        "client_id": client_id,
        "accuracy": accuracy,
        "loss": loss,
        "macro_f1": macro_f1,
        "recall_min": recall_minority,
        "f1_min": f1_minority,
        "f1_maj": f1_majority,
        "model": model
    })


In [11]:
# for client_id, model in models:
#     print(f"\n=== Client {client_id} ===")
#     print("Model Hyperparameters:")
#     print(f"  C: {model.C}")
#     print(f"  Penalty: {model.penalty}")
#     print(f"  Solver: {model.solver}")
#     print(f"  Max Iter: {model.max_iter}")
#     print(f"  Class Weight: {model.class_weight}")
#     print(f"  Multi-class: {model.multi_class}")
#     print(f"  Fit Intercept: {model.fit_intercept}")
#     print(f"  Intercept Scaling: {model.intercept_scaling}")
#     print(f"  Warm Start: {model.warm_start}")
#     print(f"  Verbose: {model.verbose}")
    
#     print("\nModel Weights (coef_):")
#     print(model.coef_)
    
#     print("\nModel Bias (intercept_):")
#     print(model.intercept_)


In [12]:
import numpy as np
import copy

def fed_avg(models):
    n = len(models)
    avg_model = copy.deepcopy(models[0][1])

    coef_sum = np.sum([model.coef_ for _, model in models], axis=0)
    intercept_sum = np.sum([model.intercept_ for _, model in models], axis=0)

    avg_model.coef_ = coef_sum / n
    avg_model.intercept_ = intercept_sum / n

    return avg_model


In [13]:
best = max(metrics, key=lambda m: m["recall_min"])
best_model = best["model"]
params = best_model.get_params()




global_model = fed_avg(models)

# Step 2: Identify best performing client (say by macro_f1 or recall_minority)
best_client = max(metrics, key=lambda m: m["macro_f1"])
best_model = best_client["model"]

# Step 3: Copy ALL hyperparameters from best client model
global_model.set_params(**best_model.get_params())

global_model



AttributeError: Coefficients are not defined for Booster type None

In [7]:
for key, val in global_model.get_params().items():
    print(f"{key}: {val}")


C: 1.0
class_weight: balanced
dual: False
fit_intercept: True
intercept_scaling: 1
l1_ratio: None
max_iter: 1000
multi_class: deprecated
n_jobs: None
penalty: l2
random_state: None
solver: lbfgs
tol: 0.0001
verbose: 0
warm_start: False


In [8]:
from sklearn.linear_model import LogisticRegression
model = LogisticRegression(
    penalty='l2',
    C=0.1,  # More regularization to reduce overfitting
    class_weight='balanced',  # Important for handling imbalance
    solver='saga',  # Supports elastic-net (useful if you consider sparse features later)
    max_iter=3000,  # Increased to ensure convergence
    tol=1e-4,  # Tighter tolerance for more stable convergence
    fit_intercept=True,
    warm_start=True,  # Allows incremental updates (useful in FedAvg)
    n_jobs=-1,  # Parallel processing
    verbose=0,
    random_state=42  # For reproducibility
)

In [9]:
global_blob = pickle.dumps(model)

In [11]:
import mysql.connector
import pickle
from sklearn.linear_model import LogisticRegression





conn_config = {
    'host': '127.0.0.1',
    'user': 'centralAuth',
    'password': 'messi10',
    'database': 'fl_database'
}
conn = mysql.connector.connect(**conn_config)
cursor = conn.cursor()


query = "INSERT INTO central_updates (model_id, version, model_blob, model_name) VALUES (%s, %s, %s, %s)"
cursor.execute(query, (1, 2, global_blob, 'LogisticRegression'))

# cursor.execute(f"INSERT INTO central_models (model_id, version, model_blob) VALUES (1, 1, {model_blob})")
conn.commit()
cursor.close()
conn.close()


**example clients**

In [59]:
import mysql.connector
import pickle
from sklearn.linear_model import LogisticRegression





conn_config = {
    'host': '127.0.0.1',
    'user': 'centralAuth',
    'password': 'messi10',
    'database': 'fl_database'
}
conn = mysql.connector.connect(**conn_config)
cursor = conn.cursor()


cursor.execute("SELECT model_blob FROM central_models WHERE model_id = %s AND version = %s", (1, 1))
result = cursor.fetchone()
cursor.close()
conn.close()

if result is None:
    raise Exception("Model not found in database.")
model_blob = result[0]
model_blob


b'\x80\x04\x95K\x01\x00\x00\x00\x00\x00\x00\x8c\x1esklearn.linear_model._logistic\x94\x8c\x12LogisticRegression\x94\x93\x94)\x81\x94}\x94(\x8c\x07penalty\x94\x8c\x02l2\x94\x8c\x04dual\x94\x89\x8c\x03tol\x94G?\x1a6\xe2\xeb\x1cC-\x8c\x01C\x94G?\xf0\x00\x00\x00\x00\x00\x00\x8c\rfit_intercept\x94\x88\x8c\x11intercept_scaling\x94K\x01\x8c\x0cclass_weight\x94\x8c\x08balanced\x94\x8c\x0crandom_state\x94N\x8c\x06solver\x94\x8c\x05lbfgs\x94\x8c\x08max_iter\x94M\xf4\x01\x8c\x0bmulti_class\x94\x8c\x0bmultinomial\x94\x8c\x07verbose\x94K\x00\x8c\nwarm_start\x94\x89\x8c\x06n_jobs\x94N\x8c\x08l1_ratio\x94N\x8c\x10_sklearn_version\x94\x8c\x051.5.2\x94ub.'

In [60]:
if isinstance(model_blob, str):
    model_blob = model_blob.encode('latin1')  # Or 'utf-8' if needed
model = pickle.loads(model_blob)
model

LogisticRegression(class_weight='balanced', max_iter=500,
                   multi_class='multinomial')